In [91]:
import torch
import torch.nn as nn
import torch.optim as optim
import matplotlib.pyplot as plt
import seaborn as sns
from tqdm import tqdm

import numpy as np
from scipy.optimize import minimize
import copy
import random


import pandas as pd
import altair as alt
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

# Compressed Sensing model creation
Steps:
- Normalize: Center data around mean. (data -mean)
- GetTs: Map the full length of data onto a 2pi interval, broken equally by data length. (Used to 2pi * data length)
- GetMatrixDesign: 
    - Omega: Angular Frequency Sampling under Nyquist Theorem: Create number of frequency equal half data length
    - A: Sine and Cosine functions of each Omega
- Get Coef: 
    - GetFirst COef:
    - Optimization loop: with AdamW with 10,000 times
    - Loss function: MSE with L1 regularization (lambda 0.5)
    - Return Sparse Coef matrix
- Predict: Design matrix * Coef matrix
- Decenter: Prediction + mean

In [92]:
np.random.seed(0)

class CompresedSensingInterpolator():
    def __init__(self):
        self.dataMean = None
        self.timeSeriesLength = None

    def _normalize(self, data):
        mean = np.nanmean(data)
        self.dataMean = mean
        data = data - self.dataMean
        return data

    def _denormalize(self, data):
        if self.dataMean == None: # if _normalize hasn't been called yet
            return data
        data = data + self.dataMean
        return data

    # Sparse representation
    def _getDesignMatrix(self, ts, numBases):
        A = []
        # sample up to the nyquist frequency
        omegas = np.linspace(1, self.timeSeriesLength // 2, numBases)
        print("creating design matrix")
        loop = tqdm(total = omegas.shape[0])
        for omega in omegas:
            bi_r = np.cos(omega * ts)
            bi_i = np.sin(omega * ts)

            A.append(bi_r)
            A.append(bi_i)
            loop.update()
        loop.close()

        A = np.array(A).T

        return A, omegas

    def _getDataWithoutNones(self,dataWithNones, ts):
        '''
        use all the data that is not None
        '''
        mask = np.isnan(dataWithNones)
        dataWithNones = np.array(dataWithNones)
        data = dataWithNones[~mask]

        tsWithoutNones = ts[~mask]
        return data, tsWithoutNones

    def _getTs(self, dataWithNones):
        '''
        Time unit = total number of days
        '''
        self.timeSeriesLength = dataWithNones.shape[0]
        # ts = np.linspace(0, 2 * np.pi, self.timeSeriesLength)
        num_days = self.timeSeriesLength 
        ts = np.linspace(0, 2 * np.pi, self.timeSeriesLength)
        return ts

    def _predict(self, A, coefficients):
        return A @ coefficients

    def _getFirstGuessOfCoefficients(self, data, A):
        result = np.linalg.lstsq(A, data, rcond=None)
        coefficients = result[0]
        return coefficients

#    def _getL1Norm(self, coefficients):
#        return torch.linalg.norm(coefficients, 1)

    def _getCoefficients(self, dataWithoutNones, tsWithoutNones, numBases, method="SLSQP"):
        A, omegas = self._getDesignMatrix(tsWithoutNones, numBases)
        firstGuess = self._getFirstGuessOfCoefficients(dataWithoutNones, A)

        #device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

        # Convert everything over to tensors to use PyTorch and move to GPU if available
        #device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
        A = torch.Tensor(A)
        y = torch.Tensor(dataWithoutNones)
        thetas = torch.nn.Parameter(torch.Tensor(firstGuess))

        # Optimizer (SLSQP, OMP)
        optimTheta = optim.Adam([thetas], lr=1e-1)

        numSteps = 10000
        lamda = 0.5
        print("optimizing parameters")
        loop = tqdm(total=numSteps)
        for i in range(numSteps):
            # clear the gradient
            optimTheta.zero_grad()

            # make predictions
            yHat = A @ thetas

            # measure loss
            loss1 = torch.linalg.norm(y - yHat, 2) # 2-norm of the error
            loss2 = torch.linalg.norm(thetas, 1) # 1-norm of the parameters
            loss = loss1 + (lamda * loss2)

            # calculate backward pass
            loss.backward()
            optimTheta.step()
            loop.update()
        loop.close()

        coefficients = thetas.detach().numpy()

        return coefficients, omegas


    def _getReconstruction(self, coefficients, dataWithNones, ts, numBases, ys):
        # only model the missing times
        mask = np.isnan(dataWithNones)
        tsWithNones = ts[mask]
        A,omegas = self._getDesignMatrix(tsWithNones, numBases)
        reconstructedMissingData = self._predict(A, coefficients)
        reconstructedFullData = copy.copy(dataWithNones)
        reconstructedFullData[mask] = reconstructedMissingData
        return reconstructedFullData

    def interpolate(self, dataWithNones, numBases=100, ys=None, method="SLSQP"):
        '''
        uses compressed sensing to interpolate missing data

        numBases: the number of fourier basis functions to use
        when building the interpolation model. More = more accurate.
        '''
        normalizedDataWithNones = self._normalize(dataWithNones)

        ts = self._getTs(normalizedDataWithNones)
        dataWithoutNones, tsWithoutNones = self._getDataWithoutNones(normalizedDataWithNones, ts)
        coefficients, omegas = self._getCoefficients(dataWithoutNones, tsWithoutNones, numBases, method=method)
        normalizedReconstruction = self._getReconstruction(coefficients, normalizedDataWithNones, ts, numBases, ys)

        reconstruction = self._denormalize(normalizedReconstruction)

        return reconstruction, coefficients, omegas
    



In [93]:
df = pd.read_csv("Data/elwha.cleaned.2000-2023.csv", parse_dates=['DateTime'])

In [94]:
''' Original
def riverTempInterpolator(df, interval = 5):
    site_dfs = {}
    for site, site_group in df.groupby('Site'):
        print(f"Site {site}:")

        all_days = pd.date_range(df['DateTime'].min(), df['DateTime'].max(), freq='1H')
        all_days = pd.DataFrame(all_days, columns=["DateTime"])
        ys = all_days.merge(site_group, on='DateTime', how='left')

        ysMissing = ys.iloc[::interval, :] #sampling only every second measurment to save on memory
        print(ysMissing)
        ysMissing = np.asarray(ysMissing['Temp'])

        method="SLSQP" # "BFGS", etc. see the method paramter here -> https://docs.scipy.org/doc/scipy/reference/generated/scipy.optimize.minimize.html
        numBases = int((ysMissing.shape[0]/2) + 1)
        interpolator = CompresedSensingInterpolator()
        ysComplete = interpolator.interpolate(ysMissing, numBases=numBases, method=method)

        data = {'DateTime': np.asarray(ys.iloc[::interval, :]['DateTime']),
                'Missing': ysMissing,
                'Interpolated': ysComplete
                }
        df_interpolated = pd.DataFrame(data)
        site_dfs[site] = df_interpolated

    return site_dfs'''

' Original\ndef riverTempInterpolator(df, interval = 5):\n    site_dfs = {}\n    for site, site_group in df.groupby(\'Site\'):\n        print(f"Site {site}:")\n\n        all_days = pd.date_range(df[\'DateTime\'].min(), df[\'DateTime\'].max(), freq=\'1H\')\n        all_days = pd.DataFrame(all_days, columns=["DateTime"])\n        ys = all_days.merge(site_group, on=\'DateTime\', how=\'left\')\n\n        ysMissing = ys.iloc[::interval, :] #sampling only every second measurment to save on memory\n        print(ysMissing)\n        ysMissing = np.asarray(ysMissing[\'Temp\'])\n\n        method="SLSQP" # "BFGS", etc. see the method paramter here -> https://docs.scipy.org/doc/scipy/reference/generated/scipy.optimize.minimize.html\n        numBases = int((ysMissing.shape[0]/2) + 1)\n        interpolator = CompresedSensingInterpolator()\n        ysComplete = interpolator.interpolate(ysMissing, numBases=numBases, method=method)\n\n        data = {\'DateTime\': np.asarray(ys.iloc[::interval, :][\'Da

# Randomized sampling reconstruction

## Data Cleaning and Resampling
- Resampling from Hourly to daily frequency with AVG agg.
- Clean: remove dup datetime, add full datetime

In [95]:
# Pick a site to filter
selected_site = 'IC02'
selected_site_temp = df[df.Site == selected_site].reset_index().drop('index', axis = 1)
all_days = pd.date_range(df.DateTime.min(), df.DateTime.max(), freq='1H')


C:\Users\tuana\AppData\Local\Temp/ipykernel_25380/4073792227.py:4: FutureWarning: 'H' is deprecated and will be removed in a future version, please use 'h' instead.
  all_days = pd.date_range(df.DateTime.min(), df.DateTime.max(), freq='1H')


In [96]:
# Merge with full calendar to prevent missing datetime index. Remove duplicates for any DateTime
selected_site_temp = selected_site_temp.drop_duplicates(subset=['DateTime'])
full_hour = pd.date_range(selected_site_temp.loc[selected_site_temp.Temp.notnull(),'DateTime'].min(), selected_site_temp['DateTime'].max(), freq='1H')
full_hour = pd.DataFrame(full_hour, columns=["DateTime"])
selected_site_temp = full_hour.merge(selected_site_temp, on='DateTime', how='left')
selected_site_temp['Site'].fillna(selected_site, inplace=True)

train_data = selected_site_temp.copy()
train_data = train_data.set_index('DateTime')

# Using daily average mean as training data to reduce computational cost
train_data = train_data.groupby(['Site', train_data.index.date]).mean('Temp').reset_index()
train_data.columns = ['Site', 'DateTime', 'Temp']
train_data['DateTime'] = pd.to_datetime(train_data['DateTime'])

C:\Users\tuana\AppData\Local\Temp/ipykernel_25380/293195728.py:3: FutureWarning: 'H' is deprecated and will be removed in a future version, please use 'h' instead.
  full_hour = pd.date_range(selected_site_temp.loc[selected_site_temp.Temp.notnull(),'DateTime'].min(), selected_site_temp['DateTime'].max(), freq='1H')
C:\Users\tuana\AppData\Local\Temp/ipykernel_25380/293195728.py:6: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.


  selected_site_temp['Site'].fillna(selected_site, inplace=True)


## Preprocessing & Call for CS
- Train period define: % of head data (Holder_per)
- Random Sampling: (Train_per)
- Create Null Mask: Any data outside of training period, and random sampling turned Null -> constructed.
- Create Numbase: Follow Nyquist Sampling theorem
- Output: 
    - Interpolation: Train data (random sampling under training period), Full Truth, Full interpolated (overlap with Truth and train)


In [97]:
def riverTempInterpolator_random_sampling(df, interval = 10, site = 'IC02', train_per = 0.1, holdout_per = 0.2):
    df = df[df['Site'] == site]
    all_days = pd.date_range(df['DateTime'].min(), df['DateTime'].max(), freq='D')
    all_days = pd.DataFrame(all_days, columns=["DateTime"])
    ys = all_days.merge(df, on='DateTime', how='left')

    ys = ys.reset_index().drop('index', axis = 1)

    ysMissing = ys.copy()


    print(ysMissing)
    # Create a training mask with random size of train_per (default 10%)
    indices = np.asarray(ysMissing.index)
    train_indices = np.random.choice(indices, size = int(len(indices) * train_per), replace = False)

    # Mix in with the head holdout method to see forecast ability
    cut_index = int(len(indices)* holdout_per)

    train_indices = train_indices[train_indices <= cut_index]    

    train_indices = list(np.sort(train_indices))

    train_mask = np.in1d(indices, train_indices)
    #Set tesk data into Null, keep only Train data in the original series
    ysMissing = ysMissing['Temp']
    ysMissing[~train_mask] = None


    method="SLSQP" # "BFGS", etc. see the method paramter here -> https://docs.scipy.org/doc/scipy/reference/generated/scipy.optimize.minimize.html
    numBases = int((ysMissing.shape[0]/2) + 1)
    print(numBases)
    interpolator = CompresedSensingInterpolator()
    ysComplete, coefficient, omegas = interpolator.interpolate(ysMissing, numBases=numBases, method=method)
    data = {'DateTime': np.asarray(ys['DateTime']),
            'Train_data': ysMissing,
            'Interpolated': ysComplete,
            'Truth': ys['Temp']}
    df_interpolated = pd.DataFrame(data)
    
    cos_coeffs = coefficient[0::2]  # even indices
    sin_coeffs = coefficient[1::2]  # odd indices
    coef_matrix = {'Sin_coef': sin_coeffs,
                   'Cos_coef':cos_coeffs,
            'omegas': omegas}
    
    
    return df_interpolated, coef_matrix, coefficient


In [98]:
random.seed(527)
train_per = 0.3
holdout_per = 0.2
df_clean, coef_matrix, coef = riverTempInterpolator_random_sampling(train_data, train_per = train_per, holdout_per= holdout_per, interval = 1)


       DateTime  Site      Temp
0    2006-10-03  IC02  9.232812
1    2006-10-04  IC02  8.779167
2    2006-10-05  IC02  8.914583
3    2006-10-06  IC02  9.767708
4    2006-10-07  IC02  9.423958
...         ...   ...       ...
5533 2021-11-26  IC02       NaN
5534 2021-11-27  IC02       NaN
5535 2021-11-28  IC02       NaN
5536 2021-11-29  IC02       NaN
5537 2021-11-30  IC02       NaN

[5538 rows x 3 columns]
2770
creating design matrix


100%|██████████| 2770/2770 [00:00<00:00, 32020.85it/s]


optimizing parameters


100%|██████████| 10000/10000 [00:18<00:00, 552.40it/s]


creating design matrix


100%|██████████| 2770/2770 [00:00<00:00, 7619.14it/s]


## Result
- Filter out: No truth + no train (missing data outside of training period)
- Filter out: Training sampling
- Metric: MAE for best intepretation

In [99]:
# General Result

# Remove all where no Truth data found and no Train data found
df_clean_filtered = df_clean[~(df_clean.Train_data.isnull() & df_clean.Truth.isnull())]

df_clean_filtered = df_clean_filtered[(df_clean_filtered.Train_data.isnull()) ].set_index('DateTime', drop = False)
df_clean_filtered['absolute_diff'] = np.abs(df_clean_filtered.Truth - df_clean_filtered.Interpolated)

# Calculate mean absolute error
mae = np.mean(df_clean_filtered.absolute_diff)

# Print MAE
print("Mean Absolute Error (MAE):", mae)

Mean Absolute Error (MAE): 1.461895048616646


# Visualization
- For result only

In [100]:
# Custom theme
def custom_theme():
    return {
        'config': {
            'header': {'titleFontSize': 40,
                       'labelFontSize': 16,
                       'font': 'Sans Serif',
                       'labelColor': 'black',
                       'titleColor': 'black'},
            'axis': {'titleFontSize': 16,
                     'labelFontSize': 14,
                     'labelColor': 'dimgray',
                     'font': 'Sans Serif',
                     'titleColor': 'dimgray',
                     'grid': False,
                     'labelOffset': 5,
                     'labelPadding': 8,
                     'titlePadding': 15},
            'title': {'fontSize': 20,
                      'font': 'Sans Serif',
                      'anchor': 'middle',
                      'color': 'black',
                      'offset': 11},
            'view': {'strokeWidth': 0
                    }
        }
    }

# Apply the custom theme to the chart
alt.themes.register('custom_theme', custom_theme)
alt.themes.enable('custom_theme')

ThemeRegistry.enable('custom_theme')

# Graph function
Encodings:
- shade: Traing period
- text: MAE, Selected Site, Sapling size
- Line:
    - Color: Red for truth, Grey for reconstructed
- Point: sample

Mix legends from multiple layers

Save to higher ppi for presentation

In [101]:
def interpolated_visual(df, cutoff,mae, train_per = 0.1, ):
    min_time = train_data['DateTime'].min()
    max_time = train_data['DateTime'].max()
    cutoff_max = cutoff['stop']
    # Title texts
    chart_title = f'Reconstructed versus Actual Daily Average Temperature of Site {selected_site}'
    chart_subtitle = f'Mean Absolute Error (MAE): {mae:.2f} Celsius'

    chart = alt.Chart(df).mark_line(opacity=0.85).encode(
        x=alt.X('yearmonthdate(DateTime):T', title='Year/Month/Date', scale=alt.Scale(domain=(min_time, max_time))),
        y=alt.Y('mean(Temperature):Q', title='Temperature (Celsius)', aggregate='mean'),
        color=alt.Color('Source:N', legend=alt.Legend(title="Data Source", titleFontSize= 14, labelFontSize= 13)\
                                    ,scale=alt.Scale(domain=['Interpolated', 'Actual'],range=['grey', 'red'])
                                    ),
        tooltip=[alt.Tooltip('mean(Temperature):Q', title='Temperature'), alt.Tooltip('Source:N', title='Source')]
    ).properties(
        title={
        "text": [chart_title], #["", ""] is breaking them in 2 lines 
        "subtitle": [chart_subtitle]
        },
        width=900, height = 325
    )

    train_point = chart.transform_filter(alt.datum.Source == 'Train').mark_circle(color = 'red').encode(
        color=alt.Color('Source:N', legend=alt.Legend(title=None, labelFontSize= 13)\
                                    ,scale=alt.Scale(domain=['Train'],range=['red'])
                                    )
    )

    desc = f'Mean Absolute Error (MAE): {mae:.2f} Celsius'
    desc_trainper = [f"Trained on 36-month data" , f"Sampling size {train_per:.0%}"]

    desc_trainper_text = alt.Chart(pd.DataFrame({'desc': [desc_trainper]})).mark_text(
        fontSize=15,
        text='source',
        align='center',    
        dy=145,
        dx=-363,
        baseline='bottom', lineBreak=r'\n'
    ).encode(
        text='desc:N'
    )
    train_shade = alt.Chart(cutoff).mark_rect(opacity = 0.5, color = 'lightgrey').encode(x = 'start', x2 = 'stop')

    final_chart = alt.layer(chart, train_point).resolve_scale(
        color='independent'
    ).resolve_legend(
        color='independent'
    ) + train_shade + desc_trainper_text
    return final_chart

In [102]:
def interpolated_visual_train(df, cutoff,mae, train_per = 0.1, ):
    min_time = train_data['DateTime'].min()
    max_time = train_data['DateTime'].max()
    cutoff_max = cutoff['stop'][0]
    # Title texts
    chart_title = f'Reconstructed versus Actual Daily Average Temperature of Site {selected_site}'
    chart_subtitle = f'Mean Absolute Error (MAE): {mae:.2f} Celsius'

    chart = alt.Chart(df).mark_line(opacity=0.85).encode(
        x=alt.X('yearmonthdate(DateTime):T', title='Year/Month/Date', scale=alt.Scale(domain=(min_time, cutoff_max))),
        y=alt.Y('mean(Temperature):Q', title='Temperature (Celsius)', aggregate='mean'),
        color=alt.Color('Source:N', legend=alt.Legend(title="Data Source", titleFontSize= 14, labelFontSize= 13)\
                                    ,scale=alt.Scale(domain=['Interpolated', 'Actual'],range=['grey', 'red'])
                                    ),
        tooltip=[alt.Tooltip('mean(Temperature):Q', title='Temperature'), alt.Tooltip('Source:N', title='Source')]
    ).properties(
        title={
        "text": [chart_title], #["", ""] is breaking them in 2 lines 
        "subtitle": [chart_subtitle]
        },
        width=900, height = 325
    )

    train_point = chart.transform_filter(alt.datum.Source == 'Train').mark_circle(color = 'red').encode(
        color=alt.Color('Source:N', legend=alt.Legend(title=None, labelFontSize= 13)\
                                    ,scale=alt.Scale(domain=['Train'],range=['red'])
                                    )
    )

    desc = f'Mean Absolute Error (MAE): {mae:.2f} Celsius'
    desc_trainper = [f"Trained on 36-month data" , f"Sampling size {train_per:.0%}"]

    desc_trainper_text = alt.Chart(pd.DataFrame({'desc': [desc_trainper]})).mark_text(
        fontSize=15,
        text='source',
        align='center',    
        dy=145,
        dx=-363,
        baseline='bottom', lineBreak=r'\n'
    ).encode(
        text='desc:N'
    )
    train_shade = alt.Chart(cutoff).mark_rect(opacity = 0.5, color = 'lightgrey').encode(x = 'start', x2 = 'stop')

    final_chart = alt.layer(chart, train_point).resolve_scale(
        color='independent'
    ).resolve_legend(
        color='independent'
    ) + train_shade + desc_trainper_text
    return final_chart

In [103]:
# Adding a 'Source' column to each DataFrame
df_2 = df_clean.copy()
df_clean['Source'] = 'Interpolated'
df_2['Source'] = 'Train'
df_3 = train_data.copy()
df_3['Source'] = 'Actual'
#df_3.set_index('DateTime', drop = False, inplace = True)
#df_clean.set_index('DateTime', drop = False, inplace = True)

# Prepare data for visualization
interpolated_df = df_clean[['DateTime', 'Interpolated', 'Source']].rename(columns={'Interpolated': 'Temperature'})
train_df = df_2[['DateTime', 'Train_data', 'Source']].rename(columns={'Train_data': 'Temperature'})


selected_site_temp_ed = df_3[['DateTime', 'Temp', 'Source']].rename(columns={'Temp': 'Temperature'})

# Combine the data
combined_data = pd.concat([interpolated_df, selected_site_temp_ed, train_df])

cutoff_df = pd.DataFrame({'start' : [df_clean['DateTime'].min()], 'stop':[df_clean[~df_clean.Train_data.isnull()]['DateTime'].max()]})
combined_data
combined_data.loc[(combined_data['DateTime'] <= cutoff_df['stop'][0]) & (combined_data.Source == 'Actual'),'Temperature'] = None
result = interpolated_visual(combined_data, cutoff = cutoff_df, train_per= train_per, mae = mae)
result
#result.configure_title(fontSize=25).save('reconstructed_actual.png', ppi=800)

alt.LayerChart(...)

alt.LayerChart(...)

In [105]:
def interpolated_visual_train(df, cutoff,mae, chart_title= f'10% Random sampling observations to train and reconstruct', chart_subtitle= f'Site {selected_site}', train_per = 0.1):
    min_time = train_data['DateTime'].min()
    max_time = train_data['DateTime'].max()
    cutoff_max = cutoff['stop'][0]
    # Title texts

    chart = alt.Chart(df[df['DateTime'] <= cutoff_max]).mark_line(opacity=0.65).encode(
        x=alt.X('yearmonthdate(DateTime):T', title='Year/Month/Date', scale=alt.Scale(domain=(min_time, cutoff_max))),
        y=alt.Y('mean(Temperature):Q', title='Temperature (Celsius)', aggregate='mean'),
        color=alt.Color('Source:N', legend=alt.Legend(title="Data Source", titleFontSize= 14, labelFontSize= 13)\
                                    ,scale=alt.Scale(domain=['Interpolated','Actual'],range=['grey', 'red'])
                                    ),
        tooltip=[alt.Tooltip('mean(Temperature):Q', title='Temperature'), alt.Tooltip('Source:N', title='Source')]
    ).properties(
        title={
        "text": [chart_title], #["", ""] is breaking them in 2 lines 
        "subtitle": [chart_subtitle]
        },
        width=900, height = 325
    )

    train_point = chart.transform_filter(alt.datum.Source == 'Train').mark_circle(color = 'red', size = 75).encode(
        color=alt.Color('Source:N', legend=alt.Legend(title=None, labelFontSize= 13)\
                                    ,scale=alt.Scale(domain=['Train'],range=['red'])
                                    )
    )
    

    desc = f'Mean Absolute Error (MAE): {mae:.2f} Celsius'
    desc_trainper = [f"Trained on 24-month data" , f"Sampling size {train_per:.0%}"]
    mean_line = alt.Chart(df[df['DateTime'] <= cutoff_max]).mark_rule(opacity=0.65, strokeDash=[1,1]).encode(y = (alt.Y('mean(Temperature):Q', title = None)))
    desc_trainper_text = alt.Chart(pd.DataFrame({'desc': [desc_trainper]})).mark_text(
        fontSize=15,
        text='source',
        align='center',    
        dy=145,
        dx=-363,
        baseline='bottom', lineBreak=r'\n'
    ).encode(
        text='desc:N'
    )
    train_shade = alt.Chart(cutoff).mark_rect(opacity = 0.3, color = 'lightgrey').encode(x = 'start', x2 = 'stop')

    final_chart = alt.layer(chart, train_point).resolve_scale(
        color='independent'
    ).resolve_legend(
        color='independent'
    ) + train_shade + mean_line
    return final_chart

In [106]:
# Adding a 'Source' column to each DataFrame
df_2 = df_clean.copy()
df_clean['Source'] = 'Interpolated'
df_2['Source'] = 'Train'
df_3 = train_data.copy()
df_3['Source'] = 'Actual'
#df_3.set_index('DateTime', drop = False, inplace = True)
#df_clean.set_index('DateTime', drop = False, inplace = True)

# Prepare data for visualization
interpolated_df = df_clean[['DateTime', 'Interpolated', 'Source']].rename(columns={'Interpolated': 'Temperature'})
train_df = df_2[['DateTime', 'Train_data', 'Source']].rename(columns={'Train_data': 'Temperature'})


selected_site_temp_ed = df_3[['DateTime', 'Temp', 'Source']].rename(columns={'Temp': 'Temperature'})

# Combine the data
combined_data = pd.concat([interpolated_df, selected_site_temp_ed, train_df])

cutoff_df = pd.DataFrame({'start' : [df_clean['DateTime'].min()], 'stop':[df_clean[~df_clean.Train_data.isnull()]['DateTime'].max()]})
combined_data

# Set actual data in training period as Null for visual
#combined_data.loc[(combined_data['DateTime'] <= cutoff_df['stop'][0]) & (combined_data.Source == 'Actual'),'Temperature'] = None


result1 = interpolated_visual_train(combined_data, cutoff = cutoff_df, train_per= train_per, mae = mae)
result1
#result1.configure_title(fontSize=25).save('random_sampling.png', ppi=800)

alt.LayerChart(...)

# Test different months

# Interpolation test and Coefficients extraction
- Apply only training period as whole period to catch more shorter frequencies.
- Extract Coefficients
- Calculate days per cycles the frequency come through
- Draws the dominant frequencies

In [108]:
cutoff_index = round(train_data.index.max() * 0.2)
cutoff_date = train_data.loc[cutoff_index, 'DateTime']

In [120]:
random.seed(527)
train_data1 = train_data[train_data['DateTime'] < cutoff_date].copy()
train_per = 0.3
holdout_per = 0.2
df_clean, coef_matrix, coef = riverTempInterpolator_random_sampling(train_data1, train_per = train_per, holdout_per= 1, interval = 1)

       DateTime  Site      Temp
0    2006-10-03  IC02  9.232812
1    2006-10-04  IC02  8.779167
2    2006-10-05  IC02  8.914583
3    2006-10-06  IC02  9.767708
4    2006-10-07  IC02  9.423958
...         ...   ...       ...
1102 2009-10-09  IC02  7.837500
1103 2009-10-10  IC02  7.747917
1104 2009-10-11  IC02  6.858333
1105 2009-10-12  IC02  6.564583
1106 2009-10-13  IC02  7.182292

[1107 rows x 3 columns]
554
creating design matrix


100%|██████████| 554/554 [00:00<00:00, 73811.01it/s]

optimizing parameters


100%|██████████| 10000/10000 [00:08<00:00, 1167.98it/s]


creating design matrix


100%|██████████| 554/554 [00:00<00:00, 40979.94it/s]


In [134]:
coef

array([ 0.10364988, -0.00027828, -0.0173002 , ...,  0.00187672,
       -0.00649378, -0.01880946], dtype=float32)

In [135]:
coef = pd.DataFrame(coef_matrix)

# Amplitude = squared root of sum: squared sin and squared cos
coef['Amplitude'] = np.sqrt(coef['Sin_coef'] ** 2 + coef['Cos_coef'] ** 2)
selected_angular_freq = coef.sort_values('Amplitude', ascending = False).head(3)['omegas']



sin_coef = coef.drop('Cos_coef', axis = 1)
cos_coef = coef.drop('Sin_coef', axis = 1)

num_days = train_data1.count()[0]
time = np.linspace(0, 2 * np.pi, num_days)
plt.figure(figsize=(12, 8))

def time_frequency(sin_coef ,cos_coef ,omega, time):

    cos_component = cos_coef * np.cos(omega * time)
    sin_component = -sin_coef * np.sin(omega * time)
    signal = cos_component + sin_component
    return signal

final_signal_list = {}
# Loop through each frequency and sum their contributions
for frequency in selected_angular_freq:
    final_signal = np.zeros_like(time)
    df = coef[coef.omegas == frequency]
    for index, row in df.iterrows():
        freq = row['omegas']
        cos_coef = row['Cos_coef']
        sin_coef = row['Sin_coef']
        final_signal += time_frequency(cos_coef, sin_coef, freq , time)
        final_signal_list[freq] = final_signal

C:\Users\tuana\AppData\Local\Temp/ipykernel_25380/500019227.py:12: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  num_days = train_data1.count()[0]


<Figure size 864x576 with 0 Axes>

In [136]:
coef.sort_values('Amplitude', ascending= False)

Sin_coef  Cos_coef      omegas  Amplitude
2   -3.488605  0.447462    2.996383   3.517185
3    0.162185 -0.287370    3.994575   0.329978
15   0.205129 -0.071033   15.972875   0.217079
4    0.198898 -0.042290    4.992767   0.203344
27   0.135069  0.044096   27.951175   0.142084
..        ...       ...         ...        ...
459  0.001675  0.000909  459.169982   0.001906
498  0.001226  0.001335  498.099458   0.001813
419 -0.000413  0.001480  419.242315   0.001537
484  0.001143 -0.000545  484.124774   0.001266
9   -0.001201  0.000203    9.983725   0.001218

[554 rows x 4 columns]

In [137]:
freq_signal_df = pd.DataFrame()
for freq, signal in final_signal_list.items():
    # Create a temporary DataFrame for each (freq, signal) pair
    temp_df = pd.DataFrame(signal, columns=['Signal'])
    temp_df['Days_per_cycle'] = round(train_data1.count()[0]/(freq),2)
    temp_df['row_index'] = range(len(signal))
    temp_df['Frequency'] = freq
    # Concatenate the temporary DataFrame with the main DataFrame
    freq_signal_df = pd.concat([freq_signal_df, temp_df])

freq_signal_df


C:\Users\tuana\AppData\Local\Temp/ipykernel_25380/742695791.py:5: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  temp_df['Days_per_cycle'] = round(train_data1.count()[0]/(freq),2)
C:\Users\tuana\AppData\Local\Temp/ipykernel_25380/742695791.py:5: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  temp_df['Days_per_cycle'] = round(train_data1.count()[0]/(freq),2)
C:\Users\tuana\AppData\Local\Temp/ipykernel_25380/742695791.py:5: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value b

Signal  Days_per_cycle  row_index  Frequency
0    -3.488605          369.45          0   2.996383
1    -3.495716          369.45          1   2.996383
2    -3.501815          369.45          2   2.996383
3    -3.506898          369.45          3   2.996383
4    -3.510965          369.45          4   2.996383
...        ...             ...        ...        ...
1102  0.140516           69.30       1102  15.972875
1103  0.154932           69.30       1103  15.972875
1104  0.168073           69.30       1104  15.972875
1105  0.179831           69.30       1105  15.972875
1106  0.190109           69.30       1106  15.972875

[3321 rows x 4 columns]

In [138]:
freq_signal_df['Days_per_cycle'] = freq_signal_df['Days_per_cycle'].apply(lambda x: str(x))
freq_signal_df['Frequency'] = round(freq_signal_df['Frequency'],2).apply(lambda x: str(x))

In [139]:
alt.Chart(freq_signal_df[freq_signal_df.row_index <= 365]).mark_line().encode(
    alt.X('row_index:N', title = 'Days'\
          , axis=alt.Axis(labels=False))\
    , alt.Y('Signal:Q')\
    , alt.Color('Days_per_cycle:N').scale(scheme="tableau10")
).properties(width = 1000, title={
        "text": 'Top Contributing frequencies for temperature of Site IC02', #["", ""] is breaking them in 2 lines 
        "subtitle": 'Period: 365 days'
        }).configure_title(fontSize=25)#.save('contributingfreq_result.png', ppi=800)


alt.Chart(...)

In [115]:
pivot_df = freq_signal_df.pivot(index='row_index', columns='Days_per_cycle', values='Signal')

mainfreq_truth = pd.merge(train_data1, (pivot_df), left_index = True, right_index = True)

In [116]:
mainfreq_truth

Site   DateTime      Temp    277.13    369.45     42.65
0     IC02 2006-10-03  9.232812  0.036989 -3.457797 -0.009908
1     IC02 2006-10-04  8.779167  0.042246 -3.465865 -0.038893
2     IC02 2006-10-05  8.914583  0.047480 -3.472929 -0.067034
3     IC02 2006-10-06  9.767708  0.052691 -3.478987 -0.093721
4     IC02 2006-10-07  9.423958  0.057874 -3.484036 -0.118373
...    ...        ...       ...       ...       ...       ...
1102  IC02 2009-10-09  7.837500  0.007800 -3.397894  0.145484
1103  IC02 2009-10-10  7.747917  0.013128 -3.411273  0.124115
1104  IC02 2009-10-11  6.858333  0.018449 -3.423663  0.100053
1105  IC02 2009-10-12  6.564583  0.023760 -3.435062  0.073819
1106  IC02 2009-10-13  7.182292  0.029059 -3.445466  0.045983

[1107 rows x 6 columns]

# Interpolation vs Extrapolation
Upper part use the entire 15-year time length to train the model. Now we use only the training period to test interpolation

In [125]:
# INTERPOLATION MAE

# Remove all where no Truth data found and no Train data found
df_clean_filtered = df_clean[~(df_clean.Train_data.isnull() & df_clean.Truth.isnull())]

# Remove all training points
df_clean_filtered = df_clean_filtered[(df_clean_filtered.Train_data.isnull())]
df_clean_filtered['absolute_diff'] = np.abs(df_clean_filtered.Truth - df_clean_filtered.Interpolated)

# Calculate mean absolute error
mae = np.mean(df_clean_filtered.absolute_diff)

# Print MAE
print("Mean Absolute Error (MAE):", mae)

Mean Absolute Error (MAE): 0.7188783269290214


In [127]:
#df_clean[(df_clean.Truth - df_clean.Train_data) > 1]

# Remove all where no Truth data found and no Train data found
df_clean_filtered = df_clean[~(df_clean.Train_data.isnull() & df_clean.Truth.isnull())]

df_clean_filtered = df_clean_filtered[df_clean_filtered.Train_data.isnull()].set_index('DateTime', drop = False)
df_clean_filtered['absolute_diff'] = np.abs(df_clean_filtered.Truth - df_clean_filtered.Interpolated)

# Calculate mean absolute error
mae = np.mean(df_clean_filtered.absolute_diff)

# Print MAE
print("Mean Absolute Error (MAE):", mae)

# Adding a 'Source' column to each DataFrame
df_2 = df_clean.copy()
df_clean['Source'] = 'Interpolated'
df_2['Source'] = 'Train'
df_3 = train_data.copy()
df_3['Source'] = 'Actual'
#df_3.set_index('DateTime', drop = False, inplace = True)
#df_clean.set_index('DateTime', drop = False, inplace = True)

# Prepare data for visualization
interpolated_df = df_clean[['DateTime', 'Interpolated', 'Source']].rename(columns={'Interpolated': 'Temperature'})
train_df = df_2[['DateTime', 'Train_data', 'Source']].rename(columns={'Train_data': 'Temperature'})


selected_site_temp_ed = df_3[['DateTime', 'Temp', 'Source']].rename(columns={'Temp': 'Temperature'})

# Combine the data
combined_data = pd.concat([interpolated_df, selected_site_temp_ed, train_df])

cutoff_df = pd.DataFrame({'start' : [df_clean['DateTime'].min()], 'stop':[df_clean[~df_clean.Train_data.isnull()]['DateTime'].max()]})
combined_data

# Set actual data in training period as Null for visual
#combined_data.loc[(combined_data['DateTime'] <= cutoff_df['stop'][0]) & (combined_data.Source == 'Actual'),'Temperature'] = None


result2 = interpolated_visual_train(combined_data, cutoff = cutoff_df, train_per= train_per, mae = mae, chart_title= 'Interpolation from 30% data for Site IC02', chart_subtitle= f'Mean Absolute Error (MAE): {mae:.2f} Celsius')
result2
result2.configure_title(fontSize=25).save('interpolation.png', ppi=800)

Mean Absolute Error (MAE): 0.7188783269290214


In [128]:
alt.Chart(freq_signal_df).mark_line().encode(
    alt.X('row_index:N'), alt.Y('Signal:Q'), alt.Color('Days_per_cycle:N')
).properties(width = 1000)


alt.Chart(...)

 $$ A = \sqrt{\sin^2(\theta) \times \cos^2(\theta)}

In [129]:
main_line = alt.Chart(train_data).mark_line(color = 'red').encode(
    alt.X('DateTime:T', title = 'DateTime'),
    alt.Y('Temp:Q', title = 'Celcius')
).properties(title = 'Train and Evaluate Plan',width=1000, height = 325)\


train_shade = alt.Chart(cutoff_df).mark_rect(opacity = 0.5, color = 'lightgrey').encode(x = 'start', x2 = 'stop')

final_chart = main_line + train_shade
final_chart.configure_title(fontSize=25)\
#.save('CS_Implementation.png', ppi=800)

alt.LayerChart(...)

In [ ]:
truth_line = alt.Chart(mainfreq_truth[(mainfreq_truth['DateTime']>= '2007-01-01') & (mainfreq_truth['DateTime'] < '2008-01-01')]).mark_line().encode(
    alt.X('DateTime:T'),
    alt.Y('Temp:Q')
).properties(width = 1000)

cycle_221_line = alt.Chart(mainfreq_truth[(mainfreq_truth['DateTime']>= '2007-01-01') & (mainfreq_truth['DateTime'] < '2008-01-01')]).mark_line(color = 'red').encode(
    alt.X('DateTime:T'),
    alt.Y('Signal_denormalized:Q')
).properties(width = 1000)

truth_mean = alt.Chart(mainfreq_truth).mark_rule().encode(
    alt.Y('mean(Temp):Q')
).properties(width = 1000)

truth_line + cycle_221_line  + truth_mean

In [140]:
#coef_viz_df = pd.DataFrame({'index' : range(len(coefficients)), 'coefficients': list(coefficients)})

chart = alt.Chart(coef).mark_bar().encode(
    alt.X('omegas:N', axis=alt.Axis(labels=False), title = 'Frequency')\
           , alt.Y('Amplitude:Q')
)

chart.properties(width= 1000, title = 'Sparse representation of all temperature frequency at Site IC02').configure_title(fontSize=25)#.save('sparse_rep.png', ppi=800)

alt.Chart(...)

In [147]:
alt.Chart(freq_signal_df[freq_signal_df.row_index <= 365]).mark_line().encode(
    alt.X('row_index:N', title = 'Days'\
          , axis=alt.Axis(labels=False))\
    , alt.Y('Signal:Q')\
    , alt.Color('Days_per_cycle:N').scale(scheme="tableau10")
).properties(width = 1000, title={
        "text": 'Top Contributing frequencies for temperature of Site IC02', #["", ""] is breaking them in 2 lines 
        "subtitle": 'Period: 365 days'
        }).configure_title(fontSize=25)#.save('contributingfreq_result.png', ppi=800)


alt.Chart(...)

In [142]:
# Calculate mean and standard deviation of the amplitudes
mean_amplitude = coef['Amplitude'].mean()
std_amplitude = coef['Amplitude'].std()

# Calculate the Z-score threshold for the upper 10%
z_score_threshold = 1.282  # Approximately for the upper 10% in a one-tailed normal distribution

# Calculate the upper threshold as mean + Z-score_threshold * std_dev
upper_threshold = mean_amplitude + z_score_threshold * std_amplitude
# Identify data points where the amplitude exceeds the 95% confidence interval
outliers = coef[coef['Amplitude'] >= upper_threshold]
outliers

Sin_coef  Cos_coef    omegas  Amplitude
2 -3.488605  0.447462  2.996383   3.517185
3  0.162185 -0.287370  3.994575   0.329978

Using 90% statistical significant threshold, only 2 is significant

In [143]:
freq_signal_df

Signal Days_per_cycle  row_index Frequency
0    -3.488605         369.45          0       3.0
1    -3.495716         369.45          1       3.0
2    -3.501815         369.45          2       3.0
3    -3.506898         369.45          3       3.0
4    -3.510965         369.45          4       3.0
...        ...            ...        ...       ...
1102  0.140516           69.3       1102     15.97
1103  0.154932           69.3       1103     15.97
1104  0.168073           69.3       1104     15.97
1105  0.179831           69.3       1105     15.97
1106  0.190109           69.3       1106     15.97

[3321 rows x 4 columns]

In [144]:
# Assuming freq_signal_df is already defined and imported
chart = alt.Chart(freq_signal_df[freq_signal_df['Days_per_cycle'] == '369.45']).mark_line(color = 'red').encode(
    x=alt.X('row_index:N', axis=alt.Axis(labels=False), title = None),
    y=alt.Y('Signal:Q', title = None),
).properties(
    width=1000, height = 85
)

chart.properties(title = 'Contributing Frequencies').configure_title(fontSize=25)#.save('contributing_signal.png', ppi=800)


alt.Chart(...)

## Presentation graphs (Unrelated)

In [ ]:
demo_df = mainfreq_truth[['final_signal']].copy()
demo_df['Source'] = 'Original Signal'
demo_bestfreq = freq_signal_df[freq_signal_df['Days_per_cycle'] == '221.72'][['Signal']].copy()
demo_bestfreq['Source'] = 'Dominant Frequency'
demo_bestfreq.columns = ['final_signal', 'Source']
demo_final_df = pd.concat([demo_df, demo_bestfreq], axis = 0)

In [ ]:
demo_final_df.reset_index(inplace= True)

In [ ]:
demo_final_df

In [ ]:
original_freq = alt.Chart(demo_final_df).mark_line().encode(
    x=alt.X('index:N', axis=alt.Axis(labels=False), title= 'Time'),
    y=alt.Y('final_signal:Q', title = 'Amplitude'), color = alt.Color('Source:N', scale=alt.Scale(domain=['Original Signal', 'Dominant Frequency'])
)).properties(width = 1000, height = 300, title = 'Original Signal vs Dominant Frequency')

original_freq.configure_title(fontSize=25).save('Reconstructed Frequency.png', ppi=800)